In [1]:
import os
import glob
import spacy
import pandas as pd
import numpy as np
from spacy.tokenizer import Tokenizer
from spacy.lang.en import English
import gensim
import string
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk

In [38]:
#[[w for w in s.split()] for s in data.split('.')]

[['In',
  '1721,',
  'Boston',
  'experienced',
  'its',
  'worst',
  'outbreak',
  'of',
  'smallpox',
  '(also',
  'known',
  'as',
  'variola)'],
 ['5,759',
  'people',
  'out',
  'of',
  'around',
  '10,600',
  'in',
  'Boston',
  'were',
  'infected',
  'and',
  '844',
  'were',
  'recorded',
  'to',
  'have',
  'died',
  'between',
  'April',
  '1721',
  'and',
  'February',
  '1722'],
 ['The',
  'outbreak',
  'would',
  'motivate',
  'Puritan',
  'minister',
  'Cotton',
  'Mather',
  'and',
  'Harvard',
  'physician',
  'Zabdiel',
  'Boylston',
  'to',
  'variolate',
  'hundreds',
  'of',
  'Bostonians',
  'in',
  'the',
  'Thirteen',
  "Colonies'",
  'earliest',
  'experiment',
  'with',
  'public',
  'inoculation'],
 ['Their',
  'efforts',
  'would',
  'inspire',
  'further',
  'use',
  'and',
  'research',
  'of',
  'variolation',
  'for',
  'immunizing',
  'people',
  'from',
  'smallpox,',
  'placing',
  'the',
  'Massachusetts',
  'Bay',
  'Colony',
  'at',
  'the',
  'epi

In [2]:
os.chdir("C:/Users/raymo/code/pin-lpt/uncancelled_master/data/WikipediaEditHistory")
df = pd.read_csv('wiki_edit_content_1.csv')

In [3]:
df.drop(columns=['Unnamed: 0'], inplace=True)

In [4]:
df_small = df[:][:100]

In [1]:
with open('english_stopwords.txt', 'r') as f:
    stop_words = [line.strip() for line in f]

FileNotFoundError: [Errno 2] No such file or directory: 'english_stopwords.txt'

In [16]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\raymo\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping taggers\averaged_perceptron_tagger.zip.


True

In [43]:
def rev_punc(text):
    for punctuation in string.punctuation:
        text = text.replace(punctuation,'') 
    return text

def cre_low(text):
    word_tokens = word_tokenize(text) 
    text = [w.lower() for w in word_tokens]
    return ' '.join(text)

def rev_num(text):
    word_tokens = word_tokenize(text) 
    text = [w for w in word_tokens if not w.isdigit()] 
    return ' '.join(text)

def rev_stop(text):
    word_tokens = word_tokenize(text) 
    text = [w for w in word_tokens if not w in stop_words] 
    return ' '.join(text)

def keep_noun(text):
    word_tokens = word_tokenize(text) 
    text = [w for (w, pos) in nltk.pos_tag(word_tokens) if pos == 'NN' or pos == 'JJ'] 
    return ' '.join(text)

stemmer = SnowballStemmer("english")
def word_lem(text):
    word_tokens = word_tokenize(text)
    text = [stemmer.stem(w) for w in word_tokens]
    return ' '.join(text)

words = set(nltk.corpus.words.words())
def rev_nonen(text):
    word_tokens = word_tokenize(text) 
    text = [w for w in word_tokens if w in words] 
    return ' '.join(text)

In [44]:
df['clean_text'] = df['content'].apply(rev_punc).apply(cre_low).apply(rev_num).apply(rev_stop).apply(keep_noun).apply(word_lem).apply(rev_nonen)

In [45]:
df['clean_text'][0]

'polish death camp polish camp news public world war holocaust murder holocaust death polish amend act nation law polish public polish nation collect human war actual scholar artist understood law use polish death camp polish camp cooper joint statement sentiment context world war polish result german action polish ethnic camp german contrast franc direct german puppet western prewar annex room german eastern rest general govern general govern intern polish german general plan comparison polish polish resist german help fellow pogrom war hide assist murder polish number aid high count righteous kind help punish death helper world war express rational express polish death death camp polish govern franc unit kingdom intern news term network news mass broadcast council use term fact polish law politician yair express polish death meet german critic express suggest fact polish historian express post board new york broadcast council yad misrepresent white spokesman use strict dead wrong unf

In [140]:
docs = []
for i in range(len(df)):
    docs.append([df['clean_text'][i]])

In [171]:
from collections import Counter

In [301]:
docs_common = []
for  i in range(len(df)):
    Co = Counter(word_tokenize(docs[i][0]))
    most_occur = Co.most_common(70)
    docs_common.append([most_occur[i][0] for i in range(len(most_occur))])

In [302]:
docs_common[0]

['polish',
 'death',
 'camp',
 'german',
 'holocaust',
 'express',
 'nation',
 'use',
 'govern',
 'law',
 'war',
 'news',
 'world',
 'foreign',
 'term',
 'public',
 'amend',
 'intern',
 'council',
 'refer',
 'report',
 'act',
 'resist',
 'broadcast',
 'fact',
 'post',
 'new',
 'state',
 'truth',
 'denial',
 'prime',
 'campaign',
 'murder',
 'collect',
 'understood',
 'statement',
 'action',
 'western',
 'general',
 'network',
 'meet',
 'critic',
 'historian',
 'york',
 'misrepresent',
 'book',
 'ambassador',
 'phrase',
 'i',
 'video',
 'march',
 'benjamin',
 'doubt',
 'group',
 'human',
 'cooper',
 'joint',
 'sentiment',
 'context',
 'franc',
 'direct',
 'help',
 'punish',
 'unit',
 'mass',
 'yair',
 'suggest',
 'spokesman',
 'pretext',
 'distort']

In [47]:
# def getUniqueWords(allWords) :
#     uniqueWords = [] 
#     for i in allWords:
#         if not i in uniqueWords:
#             uniqueWords.append(i)
#     return uniqueWords

In [334]:
docs = [getUniqueWords(word_tokenize(docs[i][0])) for i in range(len(df))]

polish
polish
death
death
camp
camp
polish
death
polish
polish
polish
polish
death
camp
camp
polish
polish
polish
camp
camp
camp
camp
camp
polish
death
camp
camp
polish
polish
polish
camp
camp
camp
camp
camp
news
news
news
news
news
news
news
news
news
news
news
news
polish
death
camp
camp
polish
polish
polish
camp
camp
camp
camp
camp
news
news
news
news
news
news
news
news
news
news
news
news
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
polish
death
camp
camp
polish
polish
polish
camp
camp
camp
camp
camp
news
news
news
news
news
news
news
news
news
news
news
news
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
public
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world
world


KeyboardInterrupt: 

In [284]:
docs[5]

['except common year calendar leap year calendar year common era ce ad year millennium year year decad start calendar calendar local use march os calendar leap day calendar calendar day differ os republican nation convent bus new york state hay open door trade china unit lead mine earth magnet second war end unit govern train profession club opera unit kingdom portion h second war labor labor labor boxer rebellion foreign boxer profession governor shot leader mat rebellion north shot dead western join fiscal freedom governor shot winner elect state kill work day unit kingdom unit central ship canal central intern court second war f cup tournament second war orang free state second war second war defeat labour meet hall second war general piet success club march march order new march central costa march prison old girl coal roof march queen rare visit march demand march botanist standard act unit march archaeologist sir stand unearth success club found march blood type blood group prize

In [303]:
vocab = set(x for doc in docs_common for x in doc)

In [304]:
len(vocab)

4189

In [53]:
from numpy.random import multinomial
from numpy import log, exp
from numpy import argmax
from tqdm import tqdm
import json

class MovieGroupProcess:
    def __init__(self, K=8, alpha=0.1, beta=0.1, n_iters=30):
        '''
        A MovieGroupProcess is a conceptual model introduced by Yin and Wang 2014 to
        describe their Gibbs sampling algorithm for a Dirichlet Mixture Model for the
        clustering short text documents.
        Reference: http://dbgroup.cs.tsinghua.edu.cn/wangjy/papers/KDD14-GSDMM.pdf
        Imagine a professor is leading a film class. At the start of the class, the students
        are randomly assigned to K tables. Before class begins, the students make lists of
        their favorite films. The teacher reads the role n_iters times. When
        a student is called, the student must select a new table satisfying either:
            1) The new table has more students than the current table.
        OR
            2) The new table has students with similar lists of favorite movies.
        :param K: int
            Upper bound on the number of possible clusters. Typically many fewer
        :param alpha: float between 0 and 1
            Alpha controls the probability that a student will join a table that is currently empty
            When alpha is 0, no one will join an empty table.
        :param beta: float between 0 and 1
            Beta controls the student's affinity for other students with similar interests. A low beta means
            that students desire to sit with students of similar interests. A high beta means they are less
            concerned with affinity and are more influenced by the popularity of a table
        :param n_iters:
        '''
        self.K = K
        self.alpha = alpha
        self.beta = beta
        self.n_iters = n_iters

        # slots for computed variables
        self.number_docs = None
        self.vocab_size = None
        self.cluster_doc_count = [0 for _ in range(K)]
        self.cluster_word_count = [0 for _ in range(K)]
        self.cluster_word_distribution = [{} for i in range(K)]

    @staticmethod
    def from_data(K, alpha, beta, D, vocab_size, cluster_doc_count, cluster_word_count, cluster_word_distribution):
        '''
        Reconstitute a MovieGroupProcess from previously fit data
        :param K:
        :param alpha:
        :param beta:
        :param D:
        :param vocab_size:
        :param cluster_doc_count:
        :param cluster_word_count:
        :param cluster_word_distribution:
        :return:
        '''
        mgp = MovieGroupProcess(K, alpha, beta, n_iters=30)
        mgp.number_docs = D
        mgp.vocab_size = vocab_size
        mgp.cluster_doc_count = cluster_doc_count
        mgp.cluster_word_count = cluster_word_count
        mgp.cluster_word_distribution = cluster_word_distribution
        return mgp

    @staticmethod
    def _sample(p):
        '''
        Sample with probability vector p from a multinomial distribution
        :param p: list
            List of probabilities representing probability vector for the multinomial distribution
        :return: int
            index of randomly selected output
        '''
        return [i for i, entry in enumerate(multinomial(1, p)) if entry != 0][0]

    def fit(self, docs, vocab_size):
        '''
        Cluster the input documents
        :param docs: list of list
            list of lists containing the unique token set of each document
        :param V: total vocabulary size for each document
        :return: list of length len(doc)
            cluster label for each document
        '''
        alpha, beta, K, n_iters, V = self.alpha, self.beta, self.K, self.n_iters, vocab_size

        D = len(docs)
        self.number_docs = D
        self.vocab_size = vocab_size

        # unpack to easy var names
        m_z, n_z, n_z_w = self.cluster_doc_count, self.cluster_word_count, self.cluster_word_distribution
        cluster_count = K
        d_z = [None for i in range(len(docs))]

        # initialize the clusters
        for i, doc in enumerate(docs):

            # choose a random  initial cluster for the doc
            z = self._sample([1.0 / K for _ in range(K)])
            d_z[i] = z
            m_z[z] += 1
            n_z[z] += len(doc)

            for word in doc:
                if word not in n_z_w[z]:
                    n_z_w[z][word] = 0
                n_z_w[z][word] += 1

        for _iter in tqdm(range(n_iters)):
            total_transfers = 0

            for i, doc in enumerate(docs):

                # remove the doc from it's current cluster
                z_old = d_z[i]

                m_z[z_old] -= 1
                n_z[z_old] -= len(doc)

                for word in doc:
                    n_z_w[z_old][word] -= 1

                    # compact dictionary to save space
                    if n_z_w[z_old][word] == 0:
                        del n_z_w[z_old][word]

                # draw sample from distribution to find new cluster
                p = self.score(doc)
                z_new = self._sample(p)

                # transfer doc to the new cluster
                if z_new != z_old:
                    total_transfers += 1

                d_z[i] = z_new
                m_z[z_new] += 1
                n_z[z_new] += len(doc)

                for word in doc:
                    if word not in n_z_w[z_new]:
                        n_z_w[z_new][word] = 0
                    n_z_w[z_new][word] += 1

            cluster_count_new = sum([1 for v in m_z if v > 0])
            print("In stage %d: transferred %d clusters with %d clusters populated" % (
            _iter, total_transfers, cluster_count_new))
            if total_transfers == 0 and cluster_count_new == cluster_count and _iter>25:
                print("Converged.  Breaking out.")
                break
            cluster_count = cluster_count_new
        self.cluster_word_distribution = n_z_w
        return d_z

    def score(self, doc):
        '''
        Score a document
        Implements formula (3) of Yin and Wang 2014.
        http://dbgroup.cs.tsinghua.edu.cn/wangjy/papers/KDD14-GSDMM.pdf
        :param doc: list[str]: The doc token stream
        :return: list[float]: A length K probability vector where each component represents
                              the probability of the document appearing in a particular cluster
        '''
        alpha, beta, K, V, D = self.alpha, self.beta, self.K, self.vocab_size, self.number_docs
        m_z, n_z, n_z_w = self.cluster_doc_count, self.cluster_word_count, self.cluster_word_distribution

        p = [0 for _ in range(K)]

        #  We break the formula into the following pieces
        #  p = N1*N2/(D1*D2) = exp(lN1 - lD1 + lN2 - lD2)
        #  lN1 = log(m_z[z] + alpha)
        #  lN2 = log(D - 1 + K*alpha)
        #  lN2 = log(product(n_z_w[w] + beta)) = sum(log(n_z_w[w] + beta))
        #  lD2 = log(product(n_z[d] + V*beta + i -1)) = sum(log(n_z[d] + V*beta + i -1))

        lD1 = log(D - 1 + K * alpha)
        doc_size = len(doc)
        for label in range(K):
            lN1 = log(m_z[label] + alpha)
            lN2 = 0
            lD2 = 0
            for word in doc:
                lN2 += log(n_z_w[label].get(word, 0) + beta)
            for j in range(1, doc_size +1):
                lD2 += log(n_z[label] + V * beta + j - 1)
            p[label] = exp(lN1 - lD1 + lN2 - lD2)

        # normalize the probability vector
        pnorm = sum(p)
        pnorm = pnorm if pnorm>0 else 1
        return [pp/pnorm for pp in p]

    def choose_best_label(self, doc):
        '''
        Choose the highest probability label for the input document
        :param doc: list[str]: The doc token stream
        :return:
        '''
        p = self.score(doc)
        return argmax(p),max(p)

In [324]:
#Use Most Common 50 Words
mgp = MovieGroupProcess(K=10, alpha=0.1, beta=0.1, n_iters=30)

In [325]:
y = mgp.fit(docs_common, len(vocab))

  3%|▎         | 1/30 [00:01<00:56,  1.95s/it]

In stage 0: transferred 826 clusters with 10 clusters populated


 10%|█         | 3/30 [00:05<00:50,  1.86s/it]

In stage 1: transferred 238 clusters with 10 clusters populated
In stage 2: transferred 51 clusters with 10 clusters populated


 13%|█▎        | 4/30 [00:07<00:47,  1.82s/it]

...

In stage 26: transferred 10 clusters with 10 clusters populated


 97%|█████████▋| 29/30 [00:53<00:01,  1.77s/it]

In stage 27: transferred 6 clusters with 10 clusters populated
In stage 28: transferred 9 clusters with 10 clusters populated


100%|██████████| 30/30 [00:54<00:00,  1.83s/it]

In stage 29: transferred 15 clusters with 10 clusters populated


In [307]:
def cluster_importance(mgp):
    n_z_w = mgp.cluster_word_distribution
    beta, V, K = mgp.beta, mgp.vocab_size, mgp.K
    phi = [{} for i in range(K)]        
    for z in range(K):
        for w in n_z_w[z]:
            phi[z][w] = (n_z_w[z][w]+beta)/(sum(n_z_w[z].values())+V*beta)
    return phi
phi = cluster_importance(mgp)

In [308]:
phi[1]

{'island': 0.0067368543847881246,
 'sea': 0.007903409256612908,
 'time': 0.010236519000262475,
 'civil': 0.0006124413077080113,
 'protect': 0.001195718743620403,
 'new': 0.0067368543847881246,
 'local': 0.0038204672052261656,
 'nation': 0.0076117705386567125,
 'event': 0.004112105923182362,
 'm': 0.0023622736154451864,
 'differ': 0.0014873574615765987,
 'risk': 0.0020706348974889907,
 'inform': 0.0020706348974889907,
 'wave': 0.00352882848726997,
 'second': 0.005570299512963341,
 'monitor': 0.001195718743620403,
 'level': 0.003237189769313774,
 'high': 0.0067368543847881246,
 'coast': 0.008195047974569105,
 'maximum': 0.004112105923182362,
 'wall': 0.0006124413077080113,
 'deep': 0.005278660795007145,
 'day': 0.010236519000262475,
 'rate': 0.0009040800256642072,
 'area': 0.010819796436174867,
 'plan': 0.0006124413077080113,
 'ash': 0.0009040800256642072,
 'eastern': 0.00702849310274432,
 'major': 0.0067368543847881246,
 'north': 0.009361602846393887,
 'sector': 0.0009040800256642072,
 

In [309]:
test_doc=['The United States presidential election of 2016 was the 58th quadrennial American presidential election, held on Tuesday, November 8, 2016. The Republican ticket of businessman Donald Trump and Indiana Governor Mike Pence defeated the Democratic ticket of former Secretary of State Hillary Clinton and U.S. Senator from Virginia Tim Kaine.While Clinton received about 2.9 million more votes nationwide, a margin of 2.1% of the total cast, Trump won a victory in the Electoral College, winning 30 states with 306 pledged electors out of 538, and overturned the perennial swing states of Florida, Iowa and Ohio, as well as the "blue wall" of Michigan, Pennsylvania and Wisconsin, which had been Democratic strongholds in presidential elections since the 1990s. Leading up to the election, a Trump victory was projected unlikely by most media forecasts.']

In [310]:
test_doc = [rev_nonen(word_lem(keep_noun(rev_stop(rev_num(cre_low(rev_punc(test_doc[0])))))))]

In [311]:
test_doc = getUniqueWords(word_tokenize(test_doc[0]))

In [312]:
test_doc

['unit',
 'elect',
 'republican',
 'ticket',
 'businessman',
 'trump',
 'mike',
 'democrat',
 'state',
 'margin',
 'total',
 'cast',
 'elector',
 'swing',
 'blue',
 'wall']

In [313]:
label, probability = mgp.choose_best_label(test_doc)

In [314]:
probability

0.9999999988028315

In [315]:
test_doc2 = ['The most striking outcome of the first round of the 2017 election to the French National Assembly is that less than half of the registered voters came to the polls. The participation rate of 48.7 %, down by 8.5 percentage points from the last election in 2012, is the lowest in the history of the French legislative contests since 1945. Two factors are likely to have contributed to this particularly weak participation rate. The first and obvious factor is the recent transformation of the French party system: the collapse of the traditional parties on the centre left and centre right; the far right’s loss of credibility in the preceding presidential election; and the centrist profile of the anticipated winner, unlikely to generate strong positive or negative mobilization in the electorate.Yet, there is another important culprit: high election frequency. Sunday’s election was the third round of voting in 2017 after two rounds of presidential elections. More generally, in the last three years, a French citizen could vote – depending on party competition in his or her electoral district – in up to 9 contests: municipal elections (2014, 2 rounds), European Parliament elections (2014), departmental elections (2015, 2 rounds), regional elections (2015, 2 rounds), and presidential elections (2017, 2 rounds). On top of that, French voters could also participate in two rounds of open presidential primaries organized in the run-up to the 2017 presidential elections by the main centre-right and centre-left parties as well as the Greens. This proliferation of elections is unprecedented in the French electoral history. Just a few decades ago, the number of participatory demands on French citizens was substantially lower. For instance, in the three years preceding the legislative election of 1978, there were at maximum 4 opportunities to vote: departmental elections (1976, 2 rounds but only half of the electorate was eligible to vote) and municipal elections (1977, 2 rounds).']

In [316]:
test_doc2 = [rev_nonen(word_lem(keep_noun(rev_stop(rev_num(cre_low(rev_punc(test_doc2[0])))))))]
test_doc2 = getUniqueWords(word_tokenize(test_doc2[0]))

In [328]:
label2, probability2 = mgp.choose_best_label(test_doc2)

In [329]:
(label2, probability2)

(1, 0.9999999997632141)

In [319]:
test_doc3 = ['The development of an automatic debating system naturally involves advancing research in a range of artificial intelligence fields. This page presents several annotated data sets developed as part of Project Debater to facilitate this research. It is organized by research sub-fields explained below.Argument Mining is a prominent research frontier. Within this field, we distinguish between Argument Detection - the detection and segmentation of argument components such as claims and evidence; and Argument Stance Classification – determining the polarity of an argument component with respect to a given topic.Beyond argument mining, a debating system should face the challenge of interactivity i.e., the ability to understand and rebut the text of the opponent’s speech. Debate Speech Analysis is a new research field that focuses on this challenge.Another important aspect of a debating system is the ability to interact with its surroundings in a human-like manner. Namely, it should be able to articulate arguments and listen to arguments made by others. Regarding the former, the Text to Speech system must demonstrate human-like expressiveness to keep human listeners engaged. The latter may call for Speech-to-text systems that are especially designed for a debating scenario.Finally, a debating system should naturally rely on more fundamental NLP capabilities. One example is the ability to assess the semantic relatedness of various pieces of texts and glue these into a coherent narrative. The system should also have the ability to identify the basic concepts mentioned in the text. The corresponding benchmark data we released thus far in this context are described in the section on Basic NLP.']

In [320]:
test_doc3 = [rev_nonen(word_lem(keep_noun(rev_stop(rev_num(cre_low(rev_punc(test_doc3[0])))))))]
test_doc3 = getUniqueWords(word_tokenize(test_doc3[0]))

In [321]:
test_doc3

['develop',
 'automat',
 'research',
 'rang',
 'page',
 'project',
 'mine',
 'frontier',
 'field',
 'distinguish',
 'argument',
 'detect',
 'segment',
 'polar',
 'respect',
 'face',
 'interact',
 'rebut',
 'text',
 's',
 'speech',
 'new',
 'import',
 'aspect',
 'manner',
 'listen',
 'express',
 'human',
 'fundament',
 'related',
 'various',
 'glue',
 'basic',
 'context',
 'section']

In [326]:
label3, probability3 = mgp.choose_best_label(test_doc3)

In [327]:
(label3, probability3)

(4, 0.6777985375216716)

In [131]:
test_doc4 = ['There is also a collaboration with Los Angeles-based streetwear label Undefeated: a duo of sneakers featuring shiny gold accents and bold logos. And rounding out the footwear collection, there is a sneaker inspired by the mythological character Medusa. (While Bryant couldn’t turn anyone to stone with a look, he could certainly stare daggers with the best of them.)The last item in the Mamba Week collection is a black Lakers jersey inspired by the team’s relatively recent black alternate jersey. The jersey was co-designed by Bryant and it features a snakeskin print on the outside with black interior and 16 stars (one for each of the franchise championships) on the side panels. It’s also been reported that the Lakers are planning on wearing the Black Mamba jersey in honor of Bryant throughout the playoffs if they make it past the first round.Even before Kobe’s death, diehard hoops fans and sneakers would come out in numbers to support their beloved star. It was a testament to his legacy and the huge impact he had on the game of basketball as well as the world of athletic sneaker design. The fact that Nike is pulling out all the stops to honor Bryant again this year is just proof that the Mamba mentality will live forever—beautifully designed sneakers and all.Image may contain Clothing Apparel Shoe Footwear Sneaker and Running ShoeThe full lineup of Mamba Week kicks.Courtesy of Nike']

In [132]:
test_doc4 = [rev_nonen(word_lem(keep_noun(rev_stop(rev_num(cre_low(rev_punc(test_doc4[0])))))))]
test_doc4 = getUniqueWords(word_tokenize(test_doc4[0]))

In [330]:
label4, probability4 = mgp.choose_best_label(test_doc4)
(label4, probability4)

(7, 0.9014998386930578)

In [220]:
doc_count = np.array(mgp.cluster_doc_count)
print('Number of documents per topic :', doc_count)
print('*'*20)

Number of documents per topic : [  9   5  95   8  51  50   0   2  23 144   4  29   3  24 126  59  41  66
   2 259]
********************


In [221]:
# Topics sorted by the number of document they are allocated to
top_index = doc_count.argsort()[-10:][::-1]
print('Most important clusters (by number of docs inside):', top_index)
print('*'*20)

Most important clusters (by number of docs inside): [19  9 14  2 17 15  4  5 16 11]
********************


In [256]:
docs_all = [word_tokenize(docs_all[i][0]) for i in range(len(docs))]

In [259]:
docs_all = [item for sublist in docs_all for item in sublist]

In [268]:
co_all = Counter(docs_all)
co_all.most_common(30)

[('world', 92),
 ('season', 64),
 ('open', 59),
 ('championship', 48),
 ('champion', 26),
 ('unit', 21),
 ('i', 20),
 ('tournament', 19),
 ('cup', 18),
 ('list', 16),
 ('grand', 16),
 ('elect', 15),
 ('super', 14),
 ('profession', 14),
 ('nation', 14),
 ('general', 14),
 ('tour', 11),
 ('china', 11),
 ('intern', 11),
 ('draft', 11),
 ('new', 8),
 ('north', 8),
 ('sponsorship', 8),
 ('june', 8),
 ('august', 7),
 ('annual', 7),
 ('music', 6),
 ('summer', 6),
 ('final', 6),
 ('second', 6)]

import pyLDAvis
import tqdm
vocabulary = list(vocab)
doc_topic_dists = [mgp.score(doc) for doc in tqdm(docs)]
doc_lengths = [len(doc) for doc in tqdm(docs)]
term_counts_map = {}
for doc in tqdm(docs):
    for term in doc:
        term_counts_map[term] = term_counts_map.get(term, 0) + 1
term_counts = [term_counts_map[term] for term in tqdm(vocabulary)]

matrix = []
for cluster in mgp.cluster_word_distribution:
    total = sum([occurance for word, occurance in cluster.items()])
    row = [cluster.get(term, 0) / total for term in vocabulary]
    matrix.append(row)

vis_data = pyLDAvis.prepare(matrix, doc_topic_dists, doc_lengths, vocabulary, term_counts)
pyLDAvis.enable_notebook()
pyLDAvis.display(vis_data)